# Capstone Project - Open a Musical Theme Café in London 

## Table of contents
* [Introduction](#introduction)
* [Data](#data)
* [Methodology](#methodology)
* [Analysis](#analysis)
* [Results and Discussion](#results)
* [Conclusion](#conclusion)

## Introduction <a name="introduction"></a>

In this project we will try to find an optimal location for a cafe. Specifically, this report will be targeted to stakeholders interested in opening an **Musical Theme Cafe** in **London**, United Kingdom.

Since there are lots of cafes in London we will try to detect **locations that are not already crowded with cafes**. As this cafe is musical themed,we would also prefer locations **as close to London's West End center as possible**, where crowded with all the famous theaters in the UK.

We will use our data science powers to generate a few most promissing neighborhoods based on this criteria. Advantages of each area will then be clearly expressed so that best possible final location can be chosen by stakeholders.

## Data <a name="data"><a/>

Based on definition of our problem, factors that will influence our decission are:
* number of existing cafes in the neighborhood 
* distance of neighborhood from West End center (theater center)

We decided to use regularly spaced grid of locations, centered around city center, to define our neighborhoods.

Following data sources will be needed to extract/generate the required information:
* centers of candidate areas will be generated algorithmically and approximate addresses of centers of those areas will be obtained using **geolocator.geocode**
* number of cafes and location in every neighborhood will be obtained using **Foursquare API**
* coordinate of West End center will be obtained using **geolocator.geocode** of well known London location (Lercester Square)

### Neighborhood Candidates

Let's create latitude & longitude coordinates for centroids of our candidate neighborhoods. We will create a grid of cells covering our area of interest which is aprox. 4x4 killometers centered around West End center.

Let's first find the latitude & longitude of West End center, using specific, well known address and geolocator.

In [1]:
# import liraries
import numpy as np 
import pandas as pd
import json 
import requests
from pandas.io.json import json_normalize
import matplotlib.cm as cm
import matplotlib.colors as colors
from sklearn.cluster import KMeans
import folium

In [2]:
from geopy.geocoders import Nominatim 
def get_coordinates (address):
    try:
        geolocator = Nominatim(user_agent="coordinates_explorer", timeout=200)
        location = geolocator.geocode(address)
        lat = location.latitude
        lon = location.longitude
        return [lat, lon]
    except:
        return [None, None]
# get coordinates of Leicester Square and name it theater_certer    
address = 'Leicester Square, United Kingdom'
theater_center = get_coordinates(address)
print('Coordinate of {}: {}'.format(address, theater_center))

Coordinate of Leicester Square, United Kingdom: [51.5105992, -0.1308565]


Now let's create a grid of area candidates, equaly spaced, centered around city center and within ~2km from Leicester Square. Our neighborhoods will be defined as circular areas with a radius of 100 meters, so our neighborhood centers will be 200 meters apart.

To accurately calculate distances we need to create our grid of locations in Cartesian 2D coordinate system which allows us to calculate distances in meters (not in latitude/longitude degrees). Then we'll project those coordinates back to latitude/longitude degrees to be shown on Folium map. So let's create functions to convert between WGS84 spherical coordinate system (latitude/longitude degrees) and UTM Cartesian coordinate system (X/Y coordinates in  meters).

In [3]:
import shapely.geometry

import pyproj
from pyproj import Transformer

import math

def lonlat_to_xy(lon, lat):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=31, datum='WGS84')
    transformer = Transformer.from_proj(proj_latlon, proj_xy)
    xy = transformer.transform(lon, lat)
    return xy[0], xy[1]

def xy_to_lonlat(x, y):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=31, datum='WGS84')
    transformer = Transformer.from_proj(proj_xy, proj_latlon)
    lonlat = transformer.transform(x, y)
    return lonlat[0], lonlat[1]

def calc_xy_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return math.sqrt(dx*dx + dy*dy)

print('Coordinate transformation check')
print('-------------------------------')
print('Theater center longitude={}, latitude={}'.format(theater_center[1], theater_center[0]))
x, y = lonlat_to_xy(theater_center[1], theater_center[0])
print('Theater center UTM X={}, Y={}'.format(x, y))
lo, la = xy_to_lonlat(x, y)
print('Theater center longitude={}, latitude={}'.format(lo, la))

Coordinate transformation check
-------------------------------
Theater center longitude=-0.1308565, latitude=51.5105992
Theater center UTM X=282753.38803952804, Y=5711255.921690965
Theater center longitude=-0.13085649999999918, latitude=51.5105992


Let's create a **hexagonal grid of cells**: we offset every other row, and adjust vertical row spacing so that **every cell center is equally distant from all it's neighbors**.

In [4]:
theater_center_x, theater_center_y = lonlat_to_xy(theater_center[1], theater_center[0]) # City center in Cartesian coordinates

k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_min = theater_center_x - 2000
x_step = 200
y_min = theater_center_y - 2000 - (int(21/k)*k*200 - 4000)/2
y_step = 200 * k 

latitudes = []
longitudes = []
distances_from_center = []
xs = []
ys = []
for i in range(0, int(21/k)):
    y = y_min + i * y_step
    x_offset = 100 if i%2==0 else 0
    for j in range(0, 21):
        x = x_min + j * x_step + x_offset
        distance_from_center = calc_xy_distance(theater_center_x, theater_center_y, x, y)
        if (distance_from_center <= 2001):
            lon, lat = xy_to_lonlat(x, y)
            latitudes.append(lat)
            longitudes.append(lon)
            distances_from_center.append(distance_from_center)
            xs.append(x)
            ys.append(y)

print(len(latitudes), 'candidate neighborhood centers generated.')

364 candidate neighborhood centers generated.


Let's visualize the data we have so far: city center location and candidate neighborhood centers:

In [5]:
map_london = folium.Map(location=theater_center, zoom_start=13)
folium.Marker(theater_center, popup='Leicester Square').add_to(map_london)
for lat, lon in zip(latitudes, longitudes):
    #folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_london) 
    folium.Circle([lat, lon], radius=100, color='blue', fill=False).add_to(map_london)
    #folium.Marker([lat, lon]).add_to(map_london)
map_london

OK, we now have the coordinates of centers of neighborhoods/areas to be evaluated, equally spaced (distance from every point to it's neighbors is exactly the same) and within ~1km from Leicester Square. 

Let's now use geolocator to get approximate addresses of those locations.

In [6]:
from geopy.geocoders import Nominatim 

def get_address(la, lo):
    try:
        geolocator = Nominatim(user_agent="address_explorer", timeout=200)
        location = geolocator.reverse(la, lo)
        address=location.address
        return address
    except:
        return None
addr = get_address(theater_center[0], theater_center[1])
print('Reverse geocoding check')
print('-----------------------')
print('Address of [{}, {}] is: {}'.format(theater_center[0], theater_center[1], addr))

Reverse geocoding check
-----------------------
Address of [51.5105992, -0.1308565] is: Aspen Way, Blackwall, London Borough of Tower Hamlets, London, Greater London, England, E14 9QS, United Kingdom


In [7]:
print('Obtaining location addresses: ', end='')
addresses = []
for lat, lon in zip(latitudes, longitudes):
    address = get_address(lat, lon)
    if address is None:
        address = 'NO ADDRESS'
    address = address.replace(', United Kingdom', '') # We don't need country part of address
    addresses.append(address)
    print(' .', end='')
print(' done.')

Obtaining location addresses:  . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


In [8]:
 addresses[100:120]

['Arora Tower, 2, Blackwall Tunnel, Canary Wharf, Blackwall, London Borough of Tower Hamlets, London, Greater London, England, E14 9PQ',
 'Arora Tower, 2, Blackwall Tunnel, Canary Wharf, Blackwall, London Borough of Tower Hamlets, London, Greater London, England, E14 9PQ',
 'Arora Tower, 2, Blackwall Tunnel, Canary Wharf, Blackwall, London Borough of Tower Hamlets, London, Greater London, England, E14 9PQ',
 'Arora Tower, 2, Blackwall Tunnel, Canary Wharf, Blackwall, London Borough of Tower Hamlets, London, Greater London, England, E14 9PQ',
 'Arora Tower, 2, Blackwall Tunnel, Canary Wharf, Blackwall, London Borough of Tower Hamlets, London, Greater London, England, E14 9PQ',
 'Arora Tower, 2, Blackwall Tunnel, Canary Wharf, Blackwall, London Borough of Tower Hamlets, London, Greater London, England, E14 9PQ',
 'Arora Tower, 2, Blackwall Tunnel, Canary Wharf, Blackwall, London Borough of Tower Hamlets, London, Greater London, England, E14 9PQ',
 'Arora Tower, 2, Blackwall Tunnel, Canar

Looking good. Let's now place all this into a Pandas dataframe.

In [9]:

df_locations = pd.DataFrame({'Address': addresses,
                             'Latitude': latitudes,
                             'Longitude': longitudes,
                             'X': xs,
                             'Y': ys,
                             'Distance from center': distances_from_center})

df_locations.head(10)

Address   Latitude  Longitude  \
0  GR40, Tunnel Avenue, Greenwich Peninsula, Roya...  51.493262  -0.138313   
1  GR40, Tunnel Avenue, Greenwich Peninsula, Roya...  51.493339  -0.135437   
2  GR40, Tunnel Avenue, Greenwich Peninsula, Roya...  51.493416  -0.132560   
3  GR40, Tunnel Avenue, Greenwich Peninsula, Roya...  51.493493  -0.129683   
4  GR40, Tunnel Avenue, Greenwich Peninsula, Roya...  51.493570  -0.126807   
5  GR40, Tunnel Avenue, Greenwich Peninsula, Roya...  51.493647  -0.123930   
6  GR40, Tunnel Avenue, Greenwich Peninsula, Roya...  51.493723  -0.121054   
7  GR40, Tunnel Avenue, Greenwich Peninsula, Roya...  51.494702  -0.142735   
8  GR40, Tunnel Avenue, Greenwich Peninsula, Roya...  51.494779  -0.139858   
9  GR40, Tunnel Avenue, Greenwich Peninsula, Roya...  51.494856  -0.136982   

              X             Y  Distance from center  
0  282153.38804  5.709351e+06           1997.498436  
1  282353.38804  5.709351e+06           1946.792233  
2  282553.38804  5.709351e+06           1915.724406  
3  282753.38804  5.709351e+06           1905.255888  
4  282953.38804  5.709351e+06           1915.724406  
5  283153.38804  5.709351e+06           1946.792233  
6  283353.38804  5.709351e+06           1997.498436  
7  281853.38804  5.709524e+06           1951.922130  
8  282053.38804  5.709524e+06           1868.154169  
9  282253.38804  5.709524e+06           1802.775638

...and let's now save/persist this data into local file.

In [10]:
df_locations.to_pickle('./locations.pkl')   

### Foursquare
Now that we have our location candidates, let's use Foursquare API to get info on cafes in each neighborhood.

We're interested in venues in 'food' category, but only those that are proper cafes - pizza places, bakeries etc. are not direct competitors so we don't care about those. So we will include in out list only venues that have 'cafe' in category name.

In [11]:
food_category = '4d4b7105d754a06374d81259' # 'Root' category for all food-related venues

cafe_categories = ['4bf58dd8d48988d16d941735','4bf58dd8d48988d1e0931735'] # 'Root' category for café and coffee shop venues

def is_cafe(categories, specific_filter=None):
    cafe_words = ['café', 'coffee shop', 'coffee','cafe']
    cafe = False
    specific = False
    for c in categories:
        category_name = c[0].lower()
        category_id = c[1]
        for r in cafe_words:
            if r in category_name:
                cafe = True
                specific = True
        if category_id in specific_filter:
            specific = True
            cafe = True
    return cafe, specific

def get_categories(categories):
    return [(cat['name'], cat['id']) for cat in categories]

def format_address(location):
    address = ', '.join(location['formattedAddress'])
    address = address.replace(', United Kingdom', '')
    address = address.replace(', England', '')
    return address

client_id='H0RVNORB0NGOYAUCC2DAF24C0JS3CTYKXS5RPKEWM1TJXQWW'
client_secret='JTCXR4NA4TSVU5WMSO5RA1TO2LPJQOX2I3XDEIVSCBN2TCRS'
version = '20180605'

def get_venues_near_location(lat, lon, category, client_id, client_secret, radius=100, limit=100):
    url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&categoryId={}&radius={}&limit={}'.format(
        client_id, client_secret, version, lat, lon, category, radius, limit)
    try:
        results = requests.get(url).json()['response']['groups'][0]['items']
        venues = [(item['venue']['id'],
                   item['venue']['name'],
                   get_categories(item['venue']['categories']),
                   (item['venue']['location']['lat'], item['venue']['location']['lng']),
                   format_address(item['venue']['location']),
                   item['venue']['location']['distance']) for item in results]        
    except:
        venues = []
    return venues

In [12]:
# Let's now go over our neighborhood locations and get nearby cafes.
import pickle

def get_cafes(lats, lons):
    cafes = {}
    location_cafes = []

    print('Obtaining venues around candidate locations:', end='')
    for lat, lon in zip(lats, lons):
        # Using radius=150 to meke sure we have overlaps/full coverage so we don't miss any cafe (we're using dictionaries to remove any duplicates resulting from area overlaps)
        venues = get_venues_near_location(lat, lon, food_category, client_id, client_secret, radius=150, limit=100)
        area_cafes = []
        for venue in venues:
            venue_id = venue[0]
            venue_name = venue[1]
            venue_categories = venue[2]
            venue_latlon = venue[3]
            venue_address = venue[4]
            venue_distance = venue[5]
            is_ca,is_co = is_cafe(venue_categories, specific_filter=cafe_categories)
            if is_ca:
                x, y = lonlat_to_xy(venue_latlon[1], venue_latlon[0])
                cafe = (venue_id, venue_name, venue_latlon[0], venue_latlon[1], venue_address, venue_distance, is_co, x, y)
                if venue_distance<=100:
                    area_cafes.append(cafe)
                cafes[venue_id] = cafe
        location_cafes.append(area_cafes)
        print(' .', end='')
    print(' done.')
    return cafes, location_cafes

# Try to load from local file system in case we did this before
cafes = {}
location_cafes = []
loaded = False
try:
    with open('cafes_150.pkl', 'rb') as f:
        cafes = pickle.load(f)
    with open('location_cafes_150.pkl', 'rb') as f:
        location_cafes = pickle.load(f)
    print('Cafe data loaded.')
    loaded = True
except:
    pass

# If load failed use the Foursquare API to get the data
if not loaded:
    cafes, location_cafes = get_cafes(latitudes, longitudes)
    
    # Let's persists this in local file system
    with open('cafes_150.pkl', 'wb') as f:
        pickle.dump(cafes, f)
    with open('location_cafes_150.pkl', 'wb') as f:
        pickle.dump(location_cafes, f)

Obtaining venues around candidate locations: . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


In [13]:
# Statistics
print('Total number of cafes:', len(cafes))
print('Average number of cafets in neighborhood:', np.array([len(r) for r in location_cafes]).mean())

Total number of cafes: 198
Average number of cafets in neighborhood: 0.42032967032967034


In [14]:
print('List of all cafes')
print('-----------------------')
for r in list(cafes.values())[:10]:
    print(r)
print('...')
print('Total:', len(cafes))

List of all cafes
-----------------------
('4ae2b056f964a5204f8f21e3', 'Regency Cafe', 51.49389527652026, -0.13231140771600738, '17-19 Regency St. (near Horseferry Rd.), City of Westminster, Greater London, SW1P 4BY', 145, True, 282572.9202197246, 5709403.168359492)
('4d5f61db5b276dcb357807c6', 'Astral Cafe', 51.494701158344704, -0.13241527788843818, '8 Regency Pl (Horseferry Rd), City of Westminster, Greater London, SW1P 2EB', 89, True, 282569.54868514126, 5709493.071697018)
('4bb495885148d13a67ac523b', 'Sapori Café & Restaurant', 51.49480549750268, -0.12765355783368967, '60 Horseferry Rd, London, Greater London, SW1P 2AF', 57, True, 282900.4963106291, 5709490.530700196)
('4c7264dcad69b60c7e4483b9', "Gianni's", 51.49486063887886, -0.12713937109640466, '48 Horseferry Rd, London, Greater London, SW1P 2AF', 120, True, 282936.4416335095, 5709495.135395427)
('4dd2ab00fa767fb7079834f3', 'Burberry Cafétaria', 51.49470119499509, -0.1265488224820957, 'Horseferry House, London, Greater London',

In [15]:
print('Cafes around location')
print('---------------------------')
for i in range(20, 40):
    rs = location_cafes[i][:8]
    names = ', '.join([r[1] for r in rs])
    print('Cafes around location {}: {}'.format(i+1, names))

Cafes around location
---------------------------
Cafes around location 21: 
Cafes around location 22: XLNT, Cafe Fresco
Cafes around location 23: 
Cafes around location 24: The Wash House Cafe
Cafes around location 25: 
Cafes around location 26: 
Cafes around location 27: 
Cafes around location 28: 
Cafes around location 29: 
Cafes around location 30: 
Cafes around location 31: 
Cafes around location 32: 
Cafes around location 33: The Rail House Cafe
Cafes around location 34: 
Cafes around location 35: 
Cafes around location 36: 
Cafes around location 37: 
Cafes around location 38: Cellarium Cafe & Terrace
Cafes around location 39: 
Cafes around location 40: 


Let's now see all the collected cafes in our area of interest on map.

In [16]:
map_london = folium.Map(location=theater_center, zoom_start=13)
folium.Marker(theater_center, popup='Leicester Square').add_to(map_london)
for cas in cafes.values():
    lat = cas[2]; lon = cas[3]
    color = 'blue' 
    folium.CircleMarker([lat, lon], radius=1, color=color, fill=True, fill_color=color, fill_opacity=1).add_to(map_london)
map_london

Looking good. So now we have all the cafes in area within 1 kilometer from Leicester Square! We also know which cafes exactly are in vicinity of every neighborhood candidate center.

This concludes the data gathering phase - we're now ready to use this data for analysis to produce the report on optimal locations for a new musical theme cafe!

## Methodology <a name="methodology"><a/>

In this project we will direct our efforts on detecting areas of London's West End that have low cafe density. We will limit our analysis to area ~2km around West End center.

In first step we have collected the required **data: location and type (category) of every cafe within 2km from West End center** (Leicester Square).

Second step in our analysis will be calculation and exploration of '**cafe density**' across different areas of West End - we will use **heatmaps** to identify a few promising areas close to center with low number of cafes in general and focus our attention on those areas.

In third and final step we will focus on most promising areas and within those create **clusters of locations that meet some basic requirements** established in discussion with stakeholders: we will take into consideration locations with **no cafe in radius of 100 meters**. We will present map of all such locations but also create clusters (using **k-means clustering**) of those locations to identify general zones / neighborhoods / addresses which should be a starting point for final 'street level' exploration and search for optimal venue location by stakeholders.

## Analysis <a name="analysis"><a/>

Let's perform some basic explanatory data analysis and derive some additional info from our raw data. First let's count the **number of cafes in every area candidate**:

In [17]:
location_cafes_count = [len(cas) for cas in location_cafes]

df_locations['Cafes in area'] = location_cafes_count

print('Average number of cafes in every area with radius = 100m:', np.array(location_cafes_count).mean())

df_locations.head(10)

Average number of cafes in every area with radius = 100m: 0.42032967032967034


Address   Latitude  Longitude  \
0  GR40, Tunnel Avenue, Greenwich Peninsula, Roya...  51.493262  -0.138313   
1  GR40, Tunnel Avenue, Greenwich Peninsula, Roya...  51.493339  -0.135437   
2  GR40, Tunnel Avenue, Greenwich Peninsula, Roya...  51.493416  -0.132560   
3  GR40, Tunnel Avenue, Greenwich Peninsula, Roya...  51.493493  -0.129683   
4  GR40, Tunnel Avenue, Greenwich Peninsula, Roya...  51.493570  -0.126807   
5  GR40, Tunnel Avenue, Greenwich Peninsula, Roya...  51.493647  -0.123930   
6  GR40, Tunnel Avenue, Greenwich Peninsula, Roya...  51.493723  -0.121054   
7  GR40, Tunnel Avenue, Greenwich Peninsula, Roya...  51.494702  -0.142735   
8  GR40, Tunnel Avenue, Greenwich Peninsula, Roya...  51.494779  -0.139858   
9  GR40, Tunnel Avenue, Greenwich Peninsula, Roya...  51.494856  -0.136982   

              X             Y  Distance from center  Cafes in area  
0  282153.38804  5.709351e+06           1997.498436              0  
1  282353.38804  5.709351e+06           1946.792233              0  
2  282553.38804  5.709351e+06           1915.724406              1  
3  282753.38804  5.709351e+06           1905.255888              0  
4  282953.38804  5.709351e+06           1915.724406              0  
5  283153.38804  5.709351e+06           1946.792233              0  
6  283353.38804  5.709351e+06           1997.498436              0  
7  281853.38804  5.709524e+06           1951.922130              0  
8  282053.38804  5.709524e+06           1868.154169              0  
9  282253.38804  5.709524e+06           1802.775638              0

OK, now let's calculate the **distance to nearest cafe from every area candidate center** (not only those within 100m - we want distance to closest one, regardless of how distant it is).

In [18]:
distances_to_cafe = []

for area_x, area_y in zip(xs, ys):
    min_distance = 10000
    for res in cafes.values():
        res_x = res[7]
        res_y = res[8]
        d = calc_xy_distance(area_x, area_y, res_x, res_y)
        if d<min_distance:
            min_distance = d
    distances_to_cafe.append(min_distance)

df_locations['Distance to Cafe'] = distances_to_cafe

In [19]:
df_locations.head(10)

Address   Latitude  Longitude  \
0  GR40, Tunnel Avenue, Greenwich Peninsula, Roya...  51.493262  -0.138313   
1  GR40, Tunnel Avenue, Greenwich Peninsula, Roya...  51.493339  -0.135437   
2  GR40, Tunnel Avenue, Greenwich Peninsula, Roya...  51.493416  -0.132560   
3  GR40, Tunnel Avenue, Greenwich Peninsula, Roya...  51.493493  -0.129683   
4  GR40, Tunnel Avenue, Greenwich Peninsula, Roya...  51.493570  -0.126807   
5  GR40, Tunnel Avenue, Greenwich Peninsula, Roya...  51.493647  -0.123930   
6  GR40, Tunnel Avenue, Greenwich Peninsula, Roya...  51.493723  -0.121054   
7  GR40, Tunnel Avenue, Greenwich Peninsula, Roya...  51.494702  -0.142735   
8  GR40, Tunnel Avenue, Greenwich Peninsula, Roya...  51.494779  -0.139858   
9  GR40, Tunnel Avenue, Greenwich Peninsula, Roya...  51.494856  -0.136982   

              X             Y  Distance from center  Cafes in area  \
0  282153.38804  5.709351e+06           1997.498436              0   
1  282353.38804  5.709351e+06           1946.792233              0   
2  282553.38804  5.709351e+06           1915.724406              1   
3  282753.38804  5.709351e+06           1905.255888              0   
4  282953.38804  5.709351e+06           1915.724406              0   
5  283153.38804  5.709351e+06           1946.792233              0   
6  283353.38804  5.709351e+06           1997.498436              0   
7  281853.38804  5.709524e+06           1951.922130              0   
8  282053.38804  5.709524e+06           1868.154169              0   
9  282253.38804  5.709524e+06           1802.775638              0   

   Distance to Cafe  
0        302.008168  
1        225.723053  
2         56.018073  
3        187.949867  
4        127.140480  
5        142.461265  
6        148.426099  
7        126.816381  
8        228.625559  
9        112.010716

In [20]:
print('Average distance to closest cafe from each area center:', df_locations['Distance to Cafe'].mean())

Average distance to closest cafe from each area center: 138.15295159369416


OK, so **on average cafes can be found within ~140m** from every area center candidate. That's fairly close, so we need to filter our areas carefully!

Let's crete a map showing **heatmap / density of cafes** and try to extract some meaningfull info from that. Also, let's show **borders of London boroughs** on our map and a few circles indicating distance of 0.5km, 1km, 1.5km and 2km  from Leicester Square.

In [21]:
# the geojson data file is already downloaded in the jupyter lab
with open('london_boroughs.json') as json_data:
    london_boroughs = json.load(json_data)
def boroughs_style(feature):
    return { 'color': 'blue', 'fill': False }

In [22]:
cafe_latlons = [[ca[2], ca[3]] for ca in cafes.values()]

In [24]:
from folium import plugins
from folium.plugins import HeatMap

map_london = folium.Map(location=theater_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_london) #cartodbpositron cartodbdark_matter
HeatMap(cafe_latlons).add_to(map_london)
folium.Marker(theater_center).add_to(map_london)
folium.Circle(theater_center, radius=500, fill=False, color='white').add_to(map_london)
folium.Circle(theater_center, radius=1000, fill=False, color='white').add_to(map_london)
folium.Circle(theater_center, radius=1500, fill=False, color='white').add_to(map_london)
folium.Circle(theater_center, radius=2000, fill=False, color='white').add_to(map_london)
folium.GeoJson(london_boroughs, style_function=boroughs_style, name='geojson').add_to(map_london)
map_london

Looks like a few pockets of low cafe density closest to city center can be found **north, south, south-west and east from Leicester Square**. 


Based on this we will now focus our analysis on areas *north, south, south-west and east from Leicester Square* - we will reduce the size of our area to have a radius of **1km**. This places our location candidates mostly in boroughs **City of Westminster and Camden**.

### Camden and City of Westminster

Analysis of popular travel guides and web sites often mention Camden and City of Westminster as beautifull, interesting, rich with culture,  popular with tourists and loved by Londoners.

*"Young, colourful, cosmopolitan, Camden argues its case well as the place to be for London's trendy set. A blend of metropolitan sophistication, serious wealth (Hampstead and Regent's Park) and stark poverty (King's Cross). Camden's diversity of wealth is also mirrored in its ethnic make up. Over one fifth of the boroughs population is from an ethnic minority, yet this cheerful mix of British, Irish, African, Asian, Turkish and Jewish people just adds to Camden's wealth of character. Architecturally, Camden is also highly mixed. Council blocks dominate in the south, yet to the north, Victorian and Georgian houses offer stylish homes for those with an income to match the hype." (http://www.net-lettings.co.uk/)

*"Nestled into a bend on the north bank of the River Thames, Westminster is a perfect starting point for any London visitor. Whether drawn by the royal splendour of Buckingham Palace or the iconic chimes of Big Ben, no trip to London is complete without a visit to this neighbourhood."* (theculturetrip.com)

*"The district where punk charged onto the British music scene, London’s vibrant Camden Town is today a mishmash of shops, market stalls, historic pubs and legendary music venues." (theculturetrip.com)


Popular with tourists, booming and trendy, relatively close to city center and well connected, those boroughs appear to justify further analysis.

Since most low-cafe-count parts are in the 1km radius circle, we define the 1km circle as our new, more narrow region of interest:

In [25]:
map_london = folium.Map(location=theater_center, zoom_start=14)
HeatMap(cafe_latlons).add_to(map_london)
folium.Marker(theater_center).add_to(map_london)
folium.Circle(theater_center, radius=1000, color='white', fill=True, fill_opacity=0.4).add_to(map_london)
folium.GeoJson(london_boroughs, style_function=boroughs_style, name='geojson').add_to(map_london)
map_london

Not bad - this nicely covers all the pockets of low cafe density in Camden and Westminster closest to West End center.

Let's also create new, more dense grid of location candidates restricted to our new region of interest (let's make our location candidates 100m appart).

In [26]:
roi_center = theater_center
roi_center_lon, roi_center_lat = (theater_center[1], theater_center[0])
roi_center_x, roi_center_y = lonlat_to_xy(roi_center_lon, roi_center_lat)

k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
roi_x_min = roi_center_x - 1000
x_step = 100
roi_y_min = roi_center_y - 1000 - (int(21/k)*k*100-2000)/2
y_step = 100 * k 

roi_latitudes = []
roi_longitudes = []
roi_xs = []
roi_ys = []
for i in range(0, int(21/k)):
    y = roi_y_min + i * y_step
    x_offset = 50 if i%2==0 else 0
    for j in range(0, 21):
        x = roi_x_min + j * x_step + x_offset
        d = calc_xy_distance(roi_center_x, roi_center_y, x, y)
        if (d <= 1001):
            lon, lat = xy_to_lonlat(x, y)
            roi_latitudes.append(lat)
            roi_longitudes.append(lon)
            roi_xs.append(x)
            roi_ys.append(y)

print(len(roi_latitudes), 'candidate neighborhood centers generated.')

364 candidate neighborhood centers generated.


OK. Now let's calculate two most important things for each location candidate: **number of cafes in vicinity** (we'll use radius of **150 meters**).

In [27]:
def count_cafes_nearby(x, y, cafes, radius=150):    
    count = 0
    for ca in cafes.values():
        ca_x = ca[7]; ca_y = ca[8]
        d = calc_xy_distance(x, y, ca_x, ca_y)
        if d<=radius:
            count += 1
    return count

roi_cafe_counts = []

print('Generating data on location candidates... ', end='')
for x, y in zip(roi_xs, roi_ys):
    count = count_cafes_nearby(x, y, cafes, radius=150)
    roi_cafe_counts.append(count)
print('done.')

Generating data on location candidates... done.


In [28]:
# Let's put this into dataframe
df_roi_locations = pd.DataFrame({'Latitude':roi_latitudes,
                                 'Longitude':roi_longitudes,
                                 'X':roi_xs,
                                 'Y':roi_ys,
                                 'Cafes nearby':roi_cafe_counts
                                 })

df_roi_locations.head(10)

Latitude  Longitude             X             Y  Cafes nearby
0  51.501931  -0.134586  282453.38804  5.710303e+06             0
1  51.501969  -0.133147  282553.38804  5.710303e+06             0
2  51.502008  -0.131708  282653.38804  5.710303e+06             0
3  51.502046  -0.130270  282753.38804  5.710303e+06             1
4  51.502085  -0.128831  282853.38804  5.710303e+06             1
5  51.502123  -0.127393  282953.38804  5.710303e+06             1
6  51.502161  -0.125954  283053.38804  5.710303e+06             2
7  51.502651  -0.136797  282303.38804  5.710390e+06             0
8  51.502689  -0.135358  282403.38804  5.710390e+06             0
9  51.502728  -0.133920  282503.38804  5.710390e+06             0

OK. Let us now **filter** those locations: we're interested only in **locations with no cafes in radius of 150 meters**.

In [29]:
good_ca_count = np.array((df_roi_locations['Cafes nearby']==0))
print('Locations with no more than one cafe nearby:', good_ca_count.sum())

good_locations = good_ca_count
print('Locations with condition met:', good_locations.sum())

df_good_locations = df_roi_locations[good_locations]


Locations with no more than one cafe nearby: 150
Locations with condition met: 150


Let's see how this looks on a map.

In [30]:
good_latitudes = df_good_locations['Latitude'].values
good_longitudes = df_good_locations['Longitude'].values

good_locations = [[lat, lon] for lat, lon in zip(good_latitudes, good_longitudes)]

map_london = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_london)
HeatMap(cafe_latlons).add_to(map_london)
folium.Circle(roi_center, radius=1000, color='white', fill=True, fill_opacity=0.6).add_to(map_london)
folium.Marker(theater_center).add_to(map_london)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_london) 
folium.GeoJson(london_boroughs, style_function=boroughs_style, name='geojson').add_to(map_london)
map_london

Looking good. We now have a bunch of locations fairly close to Leicester Square (mostly in City of Westminster and Camden boroughs), and we know that each of those locations has no cafes in radius of 150m. Any of those locations is a potential candidate for a new musical theme cafe, at least based on nearby competition.

Let's now show those good locations in a form of heatmap:

In [31]:
map_london = folium.Map(location=roi_center, zoom_start=14)
HeatMap(good_locations).add_to(map_london)
folium.Marker(theater_center).add_to(map_london)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_london)
folium.GeoJson(london_boroughs, style_function=boroughs_style, name='geojson').add_to(map_london)
map_london

Looking good. What we have now is a clear indication of zones with *no* cafes at all nearby.

Let us now **cluster** those locations to create **centers of zones containing good locations**. Those zones, their centers and addresses will be the final result of our analysis. 

In [32]:
from sklearn.cluster import KMeans

number_of_clusters = 15

good_xys = df_good_locations[['X', 'Y']].values
kmeans = KMeans(n_clusters=number_of_clusters, random_state=0).fit(good_xys)

cluster_centers = [xy_to_lonlat(cc[0], cc[1]) for cc in kmeans.cluster_centers_]

map_london = folium.Map(location=roi_center, zoom_start=15)
folium.TileLayer('cartodbpositron').add_to(map_london)
HeatMap(cafe_latlons).add_to(map_london)
folium.Circle(roi_center, radius=1000, color='white', fill=True, fill_opacity=0.4).add_to(map_london)
folium.Marker(theater_center).add_to(map_london)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=200, color='green', fill=True, fill_opacity=0.25).add_to(map_london) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_london)
folium.GeoJson(london_boroughs, style_function=boroughs_style, name='geojson').add_to(map_london)
map_london

Not bad - our clusters represent groupings of most of the candidate locations and cluster centers are placed nicely in the middle of the zones 'rich' with location candidates.

Addresses of those cluster centers will be a good starting point for exploring the neighborhoods to find the best possible location based on neighborhood specifics.

Let's see those zones on a city map without heatmap, using shaded areas to indicate our clusters:

In [34]:
map_london = folium.Map(location=roi_center, zoom_start=14)
folium.Marker(theater_center).add_to(map_london)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=100, color='#00000000', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_london)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=1, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_london)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=200, color='green', fill=False).add_to(map_london) 
folium.GeoJson(london_boroughs, style_function=boroughs_style, name='geojson').add_to(map_london)
map_london

Finaly, let's **reverse geocode those candidate area centers to get the addresses** which can be presented to stakeholders.

In [35]:
candidate_area_addresses = []
print('==============================================================')
print('Addresses of centers of areas recommended for further analysis')
print('==============================================================\n')
for lon, lat in cluster_centers:
    addr = get_address(lat, lon).replace(', United Kingdom', '')
    candidate_area_addresses.append(addr)    
    x, y = lonlat_to_xy(lon, lat)
    d = calc_xy_distance(x, y, theater_center_x, theater_center_y)
    print('{}{} => {:.1f}km from Leicester Square'.format(addr, ' '*(50-len(addr)), d/1000))

Addresses of centers of areas recommended for further analysis

Fortrose Close, Blackwall, London Borough of Tower Hamlets, London, Greater London, England, E14 0GS => 0.7km from Leicester Square
Cape Henry Court, 8, Jamestown Way, Blackwall, London Borough of Tower Hamlets, London, Greater London, England, E14 2DH => 0.5km from Leicester Square
River Lea, Pretoria Road, Canning Town, London Borough of Newham, London, Greater London, England, E16 4NP => 0.7km from Leicester Square
Arora Tower, 2, Blackwall Tunnel, Canary Wharf, Blackwall, London Borough of Tower Hamlets, London, Greater London, England, E14 9PQ => 0.9km from Leicester Square
Intercontinental Hotel The O2, 1, Blackwall Tunnel, Canary Wharf, Blackwall, London Borough of Tower Hamlets, London, Greater London, England, E14 9PQ => 0.8km from Leicester Square
Cape Henry Court, 8, Jamestown Way, Blackwall, London Borough of Tower Hamlets, London, Greater London, England, E14 2DH => 0.9km from Leicester Square
Artisans House, 

This concludes our analysis. We have created 15 addresses representing centers of zones containing locations with no cafes nearby, all zones being fairly close to London's West End center (all less than 1km from Leicester Square. Although zones are shown on map with a radius of ~300 meters (green circles), their shape is actually very irregular and their centers/addresses should be considered only as a starting point for exploring area neighborhoods in search for potential restaurant locations. Most of the zones are located in City of London and Westminster boroughs, which we have identified as interesting due to being popular with tourists, fairly close to London's West End center and well connected by public transport.

In [36]:
map_london = folium.Map(location=roi_center, zoom_start=14)
folium.Circle(theater_center, radius=25, color='red', fill=True, fill_color='red', fill_opacity=1).add_to(map_london)
for lonlat, addr in zip(cluster_centers, candidate_area_addresses):
    folium.Marker([lonlat[1], lonlat[0]], popup=addr).add_to(map_london) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=100, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.05).add_to(map_london)
map_london

## Results and Discussion <a name="results"><a/>

Our analysis shows that although there are many cafes in London (~190 in our initial area of interest which was 4x4km around Leicester Square), there are pockets of low cafe density fairly close to theater center. Highest concentration of cafes was detected south-east and west from Leicester Square, so we focused our attention to areas north, south, south-west and east, corresponding to boroughs City of Westminster and Camden. 

After directing our attention to this more narrow area of interest (covering approx. 2x2km from Leicester Square) we first created a dense grid of location candidates (spaced 100m appart); those locations were then filtered so that those with cafes in radius of 150m were removed.

Those location candidates were then clustered to create zones of interest which contain greatest number of location candidates. Addresses of centers of those zones were also generated using reverse geocoding to be used as markers/starting points for more detailed local analysis based on other factors.

Result of all this is 15 zones containing largest number of potential new cafe locations based on number of and distance to existing venues. This, of course, does not imply that those zones are actually optimal locations for a new musical theme cafe! Purpose of this analysis was to only provide info on areas close to London's West End center but not crowded with existing cafes - mand other factors should also be considered. For example if the theme of the cafe is related to one particular musical then the distance to the theater which the musical performed at should also be considered. Recommended zones should therefore be considered only as a starting point for more detailed analysis which could eventually result in location which has not only no nearby competition but also other factors taken into account and all other relevant conditions met.

## Conclusion <a name="conclusion"><a/>

Purpose of this project was to identify London areas close to West End center with low number of cafes in order to aid stakeholders in narrowing down the search for optimal location for a new musical theme cafe. By calculating cafe density distribution from Foursquare data we have first identified general boroughs that justify further analysis (City of Westminster and Camden), and then generated extensive collection of locations which satisfy some basic requirements regarding existing nearby cafes. Clustering of those locations was then performed in order to create major zones of interest (containing greatest number of potential locations) and addresses of those zone centers were created to be used as starting points for final exploration by stakeholders.

Final decission on optimal restaurant location will be made by stakeholders based on specific characteristics of neighborhoods and locations in every recommended zone, taking into consideration additional factors like attractiveness of each location (proximity to park or water), levels of noise / proximity to major roads, real estate availability, prices, social and economic dynamics of every neighborhood etc.